Basic example of provision calculation when demands in buildings are calculated and the adjacency matrix is computed. Threshold - the value above which buildings will be marked as not meeting the specified value.

In [1]:
from objectnat import get_provision
import geopandas as gpd
import pandas as pd

builds = gpd.read_file("examples_data/tara_buildings.geojson")
builds.index = builds["building_id"]
services = gpd.read_file("examples_data/tara_kinder.geojson")
services.index = services["service_id"]
adjacency_matrix = pd.read_csv("examples_data/adjacency_matrix.csv",index_col="service_id")


build_prov, services_prov, links_prov = get_provision(
    buildings=builds,
    services=services,
    adjacency_matrix=adjacency_matrix,
    threshold=15,
    city_crs=32643,
)

# Visualize data
build_prov.reset_index(drop=True,inplace=True)
services_prov.reset_index(drop=True,inplace=True)
m1 = build_prov.explore()
m2 = services_prov.explore(m=m1)
m3 = links_prov.explore(m=m2)
m3

2024-03-07 18:09:42.837 | WARNING  | provisio.provision_logic:ensure_buildings:59 - 5343 rows were deleted from the 'demanded_buildings' GeoDataFrame due to null or zero values in the 'demand' column
2024-03-07 18:09:42.846 | DEBUG    | provisio.provision_logic:_calculate_provisions:124 - Calculating provision from 9 services to 823 buildings with gravity method, it may take a while ...


Example of using `get_provision()` with the minimum amount of available data. 
- To create an `adjacency_matrix` inside, you need to provide a `nx_graph` and `weight_adjacency_matrix` - the selected weight of the edge (time_min or length_meter).
- If there is no road `graph`, as in the example below, you need to pass `city_osm_id` to load the graph from osm and local `city_crs` for calculation accuracy, as well as `weight_adjacency_matrix` to create a matrix based on the selected weight. 
- If demands in buildings are absent but buildings are resettled, provide `demand_normative` (value from 0 to 1). 
- If buildings are not resettled, `demand_normative` and `population` - the total number of residents in the area under consideration should be passed.

In [2]:
from src.objectnat import get_provision
import geopandas as gpd

builds = gpd.read_file("examples_data/tara_buildings.geojson")
builds.index = builds["building_id"]
builds.drop(columns="demand",inplace=True) # Removing the 'demand' column, necessary for other examples

services = gpd.read_file("examples_data/tara_kinder.geojson")
services.index = services["service_id"]


build_prov, services_prov, links_prov = get_provision(
        buildings=builds,
        services=services,
        threshold=15,
        city_osm_id=7226665,
        city_crs=32643,
        demand_normative=0.2,
        population=28000,
        weight_adjacency_matrix= "time_min",
)

# Visualize data
build_prov.reset_index(drop=True,inplace=True)
services_prov.reset_index(drop=True,inplace=True)
m1 = build_prov.explore()
m2 = services_prov.explore(m=m1)
m3 = links_prov.explore(m=m2)
m3

2024-03-07 18:09:52.647 | WARNING  | src.objectnat.main:get_provision:263 - The adjacency matrix is not provided.
2024-03-07 18:09:52.648 | WARNING  | src.objectnat.main:get_provision:267 - The graph is not provided, attempting to load data from OSM.
2024-03-07 18:09:52.651 | WARNING  | src.objectnat.main:get_provision:285 - The 'demand' column is missing in the provided building data, attempting to calculate values.
2024-03-07 18:09:52.652 | DEBUG    | src.objectnat.main:get_demands:103 - Calculating demands according to the normative 0.2 ...
2024-03-07 18:09:52.652 | WARNING  | src.objectnat.main:get_demands:108 - Buildings are not evacuated, the 'population' attribute is missing, attempting to evacuate...
2024-03-07 18:09:52.653 | DEBUG    | src.objectnat.main:get_balanced_buildings:49 - Evacuating 28000 residents into the provided building
2024-03-07 18:09:52.655 | DEBUG    | population_restorator.balancer.houses:balance_houses:38 - Performing buildings population balancing (6166 h

2024-03-07 18:09:55.292 | DEBUG    | dongraphio.utils.graphs:get_osmnx_graph:54 - Extracting and preparing drive graph from OSM ...


2024-03-07 18:09:56.126 | DEBUG    | dongraphio.base_models:get_intermodal_graph:36 - Preparing union of city_graphs...


Joining walk graph and car graph:   0%|          | 0/2351 [00:00<?, ?it/s]

2024-03-07 18:09:56.391 | INFO     | dongraphio.base_models:get_intermodal_graph:56 - Intermodal graph done!

2024-03-07 18:09:56.392 | INFO     | dongraphio.dongraphio:get_adjacency_matrix:85 - Creating adjacency matrix based on provided graph...
2024-03-07 18:09:56.536 | DEBUG    | dongraphio.base_models:get_adjacency_matrix:92 - Calculating distances from buildings to services ...
2024-03-07 18:09:56.548 | INFO     | dongraphio.dongraphio:get_adjacency_matrix:93 - Adjacency matrix done!
2024-03-07 18:09:56.552 | WARNING  | provisio.provision_logic:ensure_buildings:59 - 2643 rows were deleted from the 'demanded_buildings' GeoDataFrame due to null or zero values in the 'demand' column
2024-03-07 18:09:56.554 | DEBUG    | provisio.provision_logic:_calculate_provisions:124 - Calculating provision from 9 services to 3523 buildings with gravity method, it may take a while ...
